<a href="https://colab.research.google.com/github/marco-siino/llm-network-testbed/blob/main/knowledge-extraction/Q2/Codestral/Codestral_LogKnowledgeExtraction_Q2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Import libraries and load the model.

In [20]:
import os
import re
import random
import time
import requests
from google.colab import files
import shutil
!pip install rouge-score

from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from rouge_score import rouge_scorer

!pip install mistralai
from mistralai import Mistral

#api_key = os.environ['7yOu0lH5XcZC1U2ZUI2uv0ghBDduhHp5']

client = Mistral(api_key='7yOu0lH5XcZC1U2ZUI2uv0ghBDduhHp5')

model = "codestral-mamba-latest"

message = [
    {
        "role": "user",
        "content": "Write a function for fibonacci"
    }
]

chat_response = client.chat.complete(
    model=model,
    messages=message
)
print(chat_response.choices[0].message.content)

Sure, here is a simple Python function that generates the Fibonacci sequence:

```python
def fibonacci(n):
    if n <= 0:
        return "Input should be a positive integer"
    elif n == 1:
        return 0
    elif n == 2:
        return 1
    else:
        a = 0
        b = 1
        for i in range(2, n):
            fib = a + b
            a = b
            b = fib
        return fib
```

You can use this function to generate the nth number in the Fibonacci sequence, where n is a positive integer. For example, `fibonacci(1)` will return 0, `fibonacci(2)` will return 1, `fibonacci(3)` will return 1, `fibonacci(4)` will return 2, and so on.


In [2]:
!nvidia-smi

/bin/bash: line 1: nvidia-smi: command not found


# Download and organize the dataset.

In [2]:
url = "https://github.com/marco-siino/llm-network-testbed/raw/refs/heads/main/knowledge-extraction/Q2/prompt_Q2-2024-06-13.zip"

output_file = "prompt_Q2-2024-06-13.zip"

os.system(f"wget -O {output_file} {url}")

0

In [3]:
!unzip prompt_Q2-2024-06-13.zip

Archive:  prompt_Q2-2024-06-13.zip
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1046.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=992.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=966.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=982.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1084.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1012.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1086.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1050.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1076.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1070.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1062.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1042.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1010.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1058.txt  
  inflating: prompt_Q2/prompt_n_hours=2_skip_hours=1088.txt  
  inflating: prompt_Q2/prompt_n_hours=

In [4]:
folder_path="prompt_Q2"
# List all files in the folder
files = os.listdir(folder_path)

# Sort the files alphabetically
files.sort()

# Function to pre-process the few shots.

In [6]:
# The following function add the Mistral Tags within the file content.
def preprocess_sample(file_contents):

                log_sample ="Given the following LOG, which dev_eui have retransmitted the same frame at least once?\n\nLOG:\n"

                parts = file_contents.split('QUESTION:')
                log_sample += parts[0]
                log_sample += "ANSWER:"

                parts = file_contents.split('ANSWER:')
                answer = parts[1]

                question = log_sample
                answer =  answer

                return question,answer


In [7]:
file_contents = """
time: 2019-05-20 06:17:19.778000, freq: 868.5, chan: 23, lsnr: 10.0, rssi: -105.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4092
time: 2019-05-20 06:26:27.954000, freq: 868.5, chan: 23, lsnr: -4.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 25, FCnt: 3848
time: 2019-05-20 06:26:34.149000, freq: 868.3, chan: 22, lsnr: 0.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 25, FCnt: 3848
time: 2019-05-20 06:38:22.054000, freq: 868.5, chan: 23, lsnr: 3.0, rssi: -111.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 23, FCnt: 3920
time: 2019-05-20 06:40:28.948000, freq: 868.3, chan: 22, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4099
time: 2019-05-20 06:40:35.076000, freq: 868.5, chan: 23, lsnr: 6.0, rssi: -109.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4099
time: 2019-05-20 06:47:13.875000, freq: 868.5, chan: 23, lsnr: 15.0, rssi: -92.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 127, size: 23, FCnt: 4050
time: 2019-05-20 06:49:00.357000, freq: 868.5, chan: 23, lsnr: 15.0, rssi: -87.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 120, size: 23, FCnt: 148
time: 2019-05-20 07:12:18.815000, freq: 868.1, chan: 21, lsnr: 0.0, rssi: -113.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 128, size: 23, FCnt: 3850
time: 2019-05-20 07:17:18.782000, freq: 868.1, chan: 21, lsnr: -4.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4093
time: 2019-05-20 07:19:13.464000, freq: 868.5, chan: 23, lsnr: -4.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 122, size: 23, FCnt: 4106
time: 2019-05-20 07:26:33.254000, freq: 868.5, chan: 23, lsnr: -9.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3849
time: 2019-05-20 07:26:39.384000, freq: 868.1, chan: 21, lsnr: -4.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3849
time: 2019-05-20 07:38:21.808000, freq: 868.3, chan: 22, lsnr: 3.0, rssi: -111.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 23, FCnt: 3921
time: 2019-05-20 07:40:28.025000, freq: 868.5, chan: 23, lsnr: -6.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4100
time: 2019-05-20 07:40:34.159000, freq: 868.5, chan: 23, lsnr: 1.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4100
time: 2019-05-20 07:47:12.982000, freq: 868.5, chan: 23, lsnr: 15.0, rssi: -90.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 127, size: 23, FCnt: 4051
time: 2019-05-20 07:48:59.461000, freq: 868.1, chan: 21, lsnr: 14.0, rssi: -88.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 120, size: 23, FCnt: 149
time: 2019-05-20 08:12:18.419000, freq: 868.1, chan: 21, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 128, size: 23, FCnt: 3851


QUESTION: Which dev_eui have retransmitted the same frame at least once in 2 hours?

ANSWER:
 dev_eui: 121
 dev_eui: 124

"""

log_sample, answer = preprocess_sample(file_contents)

print(log_sample, answer)

Given the following LOG, which dev_eui have retransmitted the same frame at least once?

LOG:

time: 2019-05-20 06:17:19.778000, freq: 868.5, chan: 23, lsnr: 10.0, rssi: -105.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4092
time: 2019-05-20 06:26:27.954000, freq: 868.5, chan: 23, lsnr: -4.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 25, FCnt: 3848
time: 2019-05-20 06:26:34.149000, freq: 868.3, chan: 22, lsnr: 0.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 25, FCnt: 3848
time: 2019-05-20 06:38:22.054000, freq: 868.5, chan: 23, lsnr: 3.0, rssi: -111.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 23, FCnt: 3920
time: 2019-05-20 06:40:28.948000, freq: 868.3, chan: 22, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4099
time: 2019-05-20 06:40:35.076000, freq: 868.5, chan: 23, lsnr: 6.0, rssi: -109.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4099
time: 2019-05-20 06:47:13.8

# Create the few-shots samples.

In [9]:
def create_few_shots_set(folder_path,nr_samples):

    # Counter to keep track of the number of files read
    count = 0

    few_shots_set = ""

    # Get a list of all files in the directory
    files = [f for f in os.listdir(folder_path) if os.path.isfile(os.path.join(folder_path, f))]

    # Shuffle the list of files. Seed set - equal to 4 - for reproducibility.
    random.Random(4).shuffle(files)

    global test_set
    test_set = files

    # Iterate through all files in the folder
    for filename in files:
        print(filename)
        # Check if the file is a text file
        if filename.endswith(".txt"):
            # Open the file and read its contents
            with open(os.path.join(folder_path, filename), 'r') as file:
                # Read the contents of the file and append it to all_contents
                file_contents = file.read()

                question, answer = preprocess_sample(file_contents)

                few_shots_set += question
                few_shots_set += answer

                # Increment the counter
                count += 1

                # Check if reached the limit of n files
                if count == nr_samples:
                    break
        test_set.remove(filename)

    return few_shots_set

In [15]:
# Specify the number of files to read
n = 3  # Example: Read the first 5 files

# Call the function to read text files in the folder and concatenate their contents
few_shots_samples = create_few_shots_set(folder_path, n)

# Print or use the concatenated contents as needed
print(few_shots_samples)

prompt_n_hours=2_skip_hours=504.txt
prompt_n_hours=2_skip_hours=688.txt
prompt_n_hours=2_skip_hours=280.txt
Given the following LOG, which dev_eui have retransmitted the same frame at least once?

LOG:
time: 2019-06-10 00:15:51.105000, freq: 868.5, chan: 23, lsnr: -9.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 122, size: 25, FCnt: 4623
time: 2019-06-10 00:19:12.470000, freq: 868.3, chan: 22, lsnr: -6.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4367
time: 2019-06-10 00:19:18.666000, freq: 868.1, chan: 21, lsnr: -3.0, rssi: -113.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4367
time: 2019-06-10 00:19:24.794000, freq: 868.5, chan: 23, lsnr: -6.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4367
time: 2019-06-10 00:33:16.470000, freq: 868.3, chan: 22, lsnr: 9.0, rssi: -105.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4618
time: 2019-06-10 00:35:03.557000, freq: 868.3, chan: 22, lsnr: -

# Chat with the model to get the results.

In [23]:
from google.colab import drive

# Monta Google Drive
drive.mount('/content/drive')

# Percorso dove vuoi salvare il file ZIP su Google Drive
path_google_drive = '/content/drive/MyDrive/codestral_results_q2.zip'

Mounted at /content/drive


In [25]:
# Define the directory path containing the results.
result_folder_name = 'codestral_results'
result_directory_path = os.path.join(os.getcwd(), result_folder_name)
dataset_path = 'prompt_Q2'

# Iterate through all the test_files
for filename in test_set:
        print(filename)
        if(os.path.isfile(result_directory_path+"/"+filename)):
          print("Already done!\n\n")
          continue
        # Check if the file is a text file
        if filename.endswith(".txt"):

            # Create the directory if it doesn't exist
            if not os.path.exists(result_directory_path):
                os.makedirs(result_directory_path)

            # Open the file and read its contents
            with open(os.path.join(dataset_path, filename), 'r') as file:
                # Read the contents of the file and append it to all_contents
                file_contents = file.read()

                chat = ""
                # Specify the number of files to read
                #n = 5  # Example: Read the first 5 files
                # Call the function to read text files in the folder and concatenate their contents
                #few_shots_samples = create_few_shots_set(folder_path, n)

                chat = few_shots_samples
                question,anwer = preprocess_sample(file_contents)

                chat+= question

                prompt = chat
                print("****.  ECCCO IL PROMPT !!!! **** ")
                print(prompt)
                print("\n\n\n\n")

                message = [
                    {
                        "role": "user",
                        "content": prompt
                    }
                ]

                success = False
                while not success:
                    try:
                        chat_response = client.chat.complete(
                            model=model,
                            messages=message
                        )
                        success = True  # Se non viene sollevata alcuna eccezione, imposta success su True
                    except Exception as e:
                        print(f"Errore: {e}. Riprovo tra 20 secondi...")
                        time.sleep(20)  # Attendi 20 secondi prima di ritentare


                result = chat_response.choices[0].message.content
                print(result+"\n\n")

                # Define the file path
                file_path = os.path.join(result_directory_path, filename)

                with open(file_path, 'w') as f:
                  # Write some content to the file
                  f.write(result)

                # Zip the result folder and download it on Drive.
                # Comprime la cartella in un file zip e salvalo su Google Drive
                shutil.make_archive(path_google_drive.replace('.zip', ''), 'zip', result_folder_name)

                # Ora puoi andare su Google Drive per scaricare il file ZIP
                print("File compresso e salvato su Google Drive.")

Streaming output truncated to the last 5000 lines.
time: 2019-06-10 00:19:18.666000, freq: 868.1, chan: 21, lsnr: -3.0, rssi: -113.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4367
time: 2019-06-10 00:19:24.794000, freq: 868.5, chan: 23, lsnr: -6.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4367
time: 2019-06-10 00:33:16.470000, freq: 868.3, chan: 22, lsnr: 9.0, rssi: -105.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4618
time: 2019-06-10 00:35:03.557000, freq: 868.3, chan: 22, lsnr: -9.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 23, FCnt: 4439
time: 2019-06-10 00:40:02.034000, freq: 868.5, chan: 23, lsnr: 15.0, rssi: -86.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 127, size: 23, FCnt: 4569
time: 2019-06-10 00:41:49.915000, freq: 868.5, chan: 23, lsnr: 15.0, rssi: -92.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 120, size: 23, FCnt: 667
time: 2019-06-10 01:07:39.868000, freq: 868.1, chan: 21, lsnr: 15.0, rs

In [17]:
# Count and print the number of file within the codestral_results folder
file_count = sum(1 for _ in os.listdir(result_folder_name) if os.path.isfile(os.path.join(result_folder_name, _)))
print(f"Number of files in the folder: {file_count}")

Number of files in the folder: 262


In [18]:
# Count and print the number of file within the codestral_results folder
file_count = sum(1 for _ in os.listdir(dataset_path) if os.path.isfile(os.path.join(dataset_path, _)))
print(f"Number of files in the folder: {file_count}")

Number of files in the folder: 546


#****** ARRIVATO QUA!!! *****

# Given the same few-shot samples ask to Codestral to generate the Python code to perform the task.

In [ ]:
prompt ="""
Given the following string of a LOG, write a Python function to OUTPUT (as in the example below) which dev_eui has retransmitted the same frame at least once.

LOG:
time: 2019-05-21 18:16:47.648000, freq: 868.5, chan: 23, lsnr: 5.0, rssi: -109.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4130
time: 2019-05-21 18:19:00.647000, freq: 868.3, chan: 22, lsnr: -5.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 122, size: 23, FCnt: 4142
time: 2019-05-21 18:25:56.343000, freq: 868.1, chan: 21, lsnr: -2.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3886
time: 2019-05-21 18:26:02.544000, freq: 868.1, chan: 21, lsnr: -7.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3886
time: 2019-05-21 18:26:08.678000, freq: 868.3, chan: 22, lsnr: -5.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3886
time: 2019-05-21 18:38:09.529000, freq: 868.3, chan: 22, lsnr: 0.0, rssi: -113.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 23, FCnt: 3958
time: 2019-05-21 18:39:57.539000, freq: 868.3, chan: 22, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4137
time: 2019-05-21 18:40:03.735000, freq: 868.3, chan: 22, lsnr: 0.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4137
time: 2019-05-21 18:46:42.609000, freq: 868.5, chan: 23, lsnr: 15.0, rssi: -92.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 127, size: 25, FCnt: 4088
time: 2019-05-21 18:48:29.241000, freq: 868.1, chan: 21, lsnr: 14.0, rssi: -90.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 120, size: 23, FCnt: 186
time: 2019-05-21 19:16:46.731000, freq: 868.3, chan: 22, lsnr: 5.0, rssi: -108.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4131
time: 2019-05-21 19:19:00.174000, freq: 868.5, chan: 23, lsnr: -8.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 122, size: 23, FCnt: 4143
time: 2019-05-21 19:25:55.447000, freq: 868.3, chan: 22, lsnr: -5.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3887
time: 2019-05-21 19:26:01.582000, freq: 868.5, chan: 23, lsnr: -5.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3887
time: 2019-05-21 19:26:07.785000, freq: 868.5, chan: 23, lsnr: -7.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3887
time: 2019-05-21 19:38:09.158000, freq: 868.5, chan: 23, lsnr: -1.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 25, FCnt: 3959
time: 2019-05-21 19:39:56.692000, freq: 868.1, chan: 21, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4138
time: 2019-05-21 19:40:02.892000, freq: 868.1, chan: 21, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4138
time: 2019-05-21 19:46:41.701000, freq: 868.5, chan: 23, lsnr: 8.0, rssi: -106.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 127, size: 25, FCnt: 4089
time: 2019-05-21 19:48:28.310000, freq: 868.1, chan: 21, lsnr: 13.0, rssi: -87.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 120, size: 23, FCnt: 187
time: 2019-05-21 20:12:05.544000, freq: 868.5, chan: 23, lsnr: 0.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 128, size: 23, FCnt: 3889


OUTPUT:
dev_eui: 121
dev_eui: 124


"""

In [ ]:
message = [
    {
        "role": "user",
        "content": prompt
    }
]

chat_response = client.chat.complete(
    model=model,
    messages=message
)

result = chat_response.choices[0].message.content
print(result+"\n\n")

Here is a Python function that calculates and prints the number of frames received per each dev_eui:

```python
def count_frames_per_device(log):
    device_frames = {}
    lines = log.split('\n')
    for line in lines:
        if 'dev_eui' in line:
            dev_eui = line.split('dev_eui:')[1].split(',')[0]
            if dev_eui in device_frames:
                device_frames[dev_eui] += 1
            else:
                device_frames[dev_eui] = 1
    for dev_eui, frames in device_frames.items():
        print(f"For DEVICE dev_eui:{dev_eui} all received frames are {frames}.")
        with open('frame_counts.txt', 'a') as f:
            f.write(f"For DEVICE dev_eui:{dev_eui} all received frames are {frames}.\n")

log = """
time: 2019-05-21 18:16:47.648000, freq: 868.5, chan: 23, lsnr: 5.0, rssi: -109.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4130
time: 2019-05-21 18:19:00.647000, freq: 868.3, chan: 22, lsnr: -5.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_

In [ ]:
# Let's write a function to use this code.
# To be adherent as much as possible to the original question we try to not change almost anything.
def count_frames_per_device(log):
    output_log = ""
    device_frames = {}
    lines = log.split('\n')
    for line in lines:
        if 'dev_eui' in line:
            dev_eui = line.split('dev_eui:')[1].split(',')[0]
            if dev_eui in device_frames:
                device_frames[dev_eui] += 1
            else:
                device_frames[dev_eui] = 1
    for dev_eui, frames in device_frames.items():
        #print(f"For DEVICE dev_eui:{dev_eui} all received frames are {frames}.")
        output_log += f"For DEVICE dev_eui:{dev_eui} all received frames are {frames}.\n"
    return output_log
        #with open('frame_counts.txt', 'a') as f:
            #f.write(f"For DEVICE dev_eui:{dev_eui} all received frames are {frames}.\n")

log = """
time: 2019-05-21 18:16:47.648000, freq: 868.5, chan: 23, lsnr: 5.0, rssi: -109.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4130
time: 2019-05-21 18:19:00.647000, freq: 868.3, chan: 22, lsnr: -5.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 122, size: 23, FCnt: 4142
time: 2019-05-21 18:25:56.343000, freq: 868.1, chan: 21, lsnr: -2.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3886
time: 2019-05-21 18:26:02.544000, freq: 868.1, chan: 21, lsnr: -7.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3886
time: 2019-05-21 18:26:08.678000, freq: 868.3, chan: 22, lsnr: -5.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3886
time: 2019-05-21 18:38:09.529000, freq: 868.3, chan: 22, lsnr: 0.0, rssi: -113.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 23, FCnt: 3958
time: 2019-05-21 18:39:57.539000, freq: 868.3, chan: 22, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4137
time: 2019-05-21 18:40:03.735000, freq: 868.3, chan: 22, lsnr: 0.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4137
time: 2019-05-21 18:46:42.609000, freq: 868.5, chan: 23, lsnr: 15.0, rssi: -92.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 127, size: 25, FCnt: 4088
time: 2019-05-21 18:48:29.241000, freq: 868.1, chan: 21, lsnr: 14.0, rssi: -90.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 120, size: 23, FCnt: 186
time: 2019-05-21 19:16:46.731000, freq: 868.3, chan: 22, lsnr: 5.0, rssi: -108.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4131
time: 2019-05-21 19:19:00.174000, freq: 868.5, chan: 23, lsnr: -8.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 122, size: 23, FCnt: 4143
time: 2019-05-21 19:25:55.447000, freq: 868.3, chan: 22, lsnr: -5.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3887
time: 2019-05-21 19:26:01.582000, freq: 868.5, chan: 23, lsnr: -5.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3887
time: 2019-05-21 19:26:07.785000, freq: 868.5, chan: 23, lsnr: -7.0, rssi: -116.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 3887
time: 2019-05-21 19:38:09.158000, freq: 868.5, chan: 23, lsnr: -1.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 25, FCnt: 3959
time: 2019-05-21 19:39:56.692000, freq: 868.1, chan: 21, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4138
time: 2019-05-21 19:40:02.892000, freq: 868.1, chan: 21, lsnr: 3.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 121, size: 23, FCnt: 4138
time: 2019-05-21 19:46:41.701000, freq: 868.5, chan: 23, lsnr: 8.0, rssi: -106.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 127, size: 25, FCnt: 4089
time: 2019-05-21 19:48:28.310000, freq: 868.1, chan: 21, lsnr: 13.0, rssi: -87.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 120, size: 23, FCnt: 187
time: 2019-05-21 20:12:05.544000, freq: 868.5, chan: 23, lsnr: 0.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 128, size: 23, FCnt: 3889
"""

count_frames_per_device(log)

'For DEVICE dev_eui: 126 all received frames are 2.\nFor DEVICE dev_eui: 122 all received frames are 2.\nFor DEVICE dev_eui: 124 all received frames are 6.\nFor DEVICE dev_eui: 123 all received frames are 2.\nFor DEVICE dev_eui: 121 all received frames are 4.\nFor DEVICE dev_eui: 127 all received frames are 2.\nFor DEVICE dev_eui: 120 all received frames are 2.\nFor DEVICE dev_eui: 128 all received frames are 1.\n'

## Let's run the code.

In [ ]:
# Define the directory path containing the results.
#folder_name = 'codestral_source_code_results/'

result_folder_name = 'codestral_source_code_results'
result_directory_path = os.path.join(os.getcwd(), result_folder_name)
dataset_path = 'prompt_Q1-2024-05-20'

#directory_path = os.path.join(os.getcwd(), folder_name)
# Create the directory if it doesn't exist
if not os.path.exists(result_folder_name):
  os.makedirs(result_folder_name)

# Iterate through all the test_files
for filename in test_set:
        file_path = result_directory_path+"/"+filename
        #print(filename)
        #print(file_path)
        if(os.path.isfile(result_directory_path+"/"+filename)):
          print("Already done!\n\n")
          continue
        # Check if the file is a text file
        if filename.endswith(".txt"):

            # Open the file and read its contents
            with open(os.path.join(dataset_path, filename), 'r') as file:
                # Read the contents of the file and append it to all_contents
                file_contents = file.read()

                # Remove the ANSWER in the original log file.
                file_contents = file_contents.split("ANSWER", 1)
                print(file_contents[0])

                result = count_frames_per_device(file_contents[0])

                print(str(result)+"\n\n")

                with open(file_path, 'w') as f:
                  # Write some content to the file
                  f.write(result)

Already done!


time: 2019-05-31 10:13:21.924000, freq: 868.3, chan: 22, lsnr: 3.0, rssi: -106.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 126, size: 23, FCnt: 4371
time: 2019-05-31 10:17:32.080000, freq: 868.5, chan: 23, lsnr: -4.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 122, size: 23, FCnt: 4384
time: 2019-05-31 10:22:25.946000, freq: 868.5, chan: 23, lsnr: -7.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 24, FCnt: 4127
time: 2019-05-31 10:22:38.294000, freq: 868.1, chan: 21, lsnr: -2.0, rssi: -114.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 24, FCnt: 4127
time: 2019-05-31 10:23:08.401000, freq: 868.3, chan: 22, lsnr: -7.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4128
time: 2019-05-31 10:36:35.177000, freq: 868.3, chan: 22, lsnr: 1.0, rssi: -112.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 123, size: 23, FCnt: 4199
time: 2019-05-31 10:36:36.193000, freq: 868.5, chan: 23, lsnr: 3.0, rssi: -111.0, SF: SF7, BW: 125, codr

# Here the function to run the syntactic evaluation at file-level and at global-level.

In [ ]:
def evaluate_results (dataset_path,result_path):
  samples_nr = 0
  global_bleu = 0
  global_rouge1_fmeasure = 0
  global_rougeL_fmeasure = 0
  # Iterate through all the test_files
  for filename in test_set:
      # Specify the paths to the files
      file1_path = result_path+filename
      file2_path = dataset_path+filename

      # Read the contents of the files
      try:
        with open(file1_path, 'r', encoding='utf-8') as file1:
          text1 = file1.read()
      except:
        continue
      try:
        with open(file2_path, 'r', encoding='utf-8') as file2:
          text2 = file2.read()
      except:
        continue

      # Find the index where "ANSWER:" starts
      answer_start_index = text2.find("ANSWER:")

      # Remove all content before and excluding "ANSWER:"
      if answer_start_index != -1:
          text2 = text2[answer_start_index + len("ANSWER:"):].strip()

      print("Sample: ", filename)

      print(text2)
      print("\n")
      print(text1)

      #dataset_corpus += text2
      #results_corpus += text1

      # Tokenize the texts
      reference = text1.split()
      candidate = text2.split()

      # Compute BLEU score
      smoothing_function = SmoothingFunction().method1
      bleu_score = sentence_bleu([reference], candidate, smoothing_function=smoothing_function)

      # Compute ROUGE score
      scorer = rouge_scorer.RougeScorer(['rouge1', 'rougeL'], use_stemmer=True)
      rouge_scores = scorer.score(text1, text2)

      # Print the results
      print(f"BLEU score: {bleu_score}")
      print(f"ROUGE-1: {rouge_scores['rouge1']}")
      print(f"ROUGE-L: {rouge_scores['rougeL']}")

      print("\n\n")


      global_bleu += bleu_score
      global_rouge1_fmeasure += rouge_scores['rouge1'].fmeasure
      global_rougeL_fmeasure += rouge_scores['rougeL'].fmeasure

      samples_nr += 1
  # Now let's print the results on the whole corpus.
  print("\n\nTHE RESULT ON THE TWO CORPORA ARE:\n")
  # Tokenize the texts
  #reference = results_corpus.split()
  #candidate = dataset_corpus.split()

  global_bleu = global_bleu/samples_nr
  global_rouge1_fmeasure = global_rouge1_fmeasure/samples_nr
  global_rougeL_fmeasure = global_rougeL_fmeasure/samples_nr

  # Print the results
  print(f"BLEU score: {global_bleu}")
  print(f"ROUGE-1: {global_rouge1_fmeasure}")
  print(f"ROUGE-L: {global_rougeL_fmeasure}")

## Let's evaluate the results of Codestral.

In [ ]:
dataset_path = "prompt_Q1-2024-05-20/"
result_path = "codestral_results/"
evaluate_results(dataset_path,result_path)

Streaming output truncated to the last 5000 lines.


ANSWER: [/INST]
For DEVICE dev_eui:120 all received frames are 0.
For DEVICE dev_eui:121 all received frames are 0.
For DEVICE dev_eui:122 all received frames are 0.
For DEVICE dev_eui:123 all received frames are 2.
For DEVICE dev_eui:124 all received frames are 1.
For DEVICE dev_eui:125 all received frames are 2.
For DEVICE dev_eui:126 all received frames are 0.
For DEVICE dev_eui:127 all received frames are 2.
For DEVICE dev_eui:128 all received frames are 2.

[INST]Given the following LOG, how many frames are received per each dev_eui?

time: 2019-06-13 06:14:30.701000, freq: 868.3, chan: 22, lsnr: -6.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4385
time: 2019-06-13 06:16:25.992000, freq: 868.1, chan: 21, lsnr: -3.0, rssi: -115.0, SF: SF7, BW: 125, codr: 4/5, dev_eui: 124, size: 23, FCnt: 4386
time: 2019-06-13 06:16:31.987000, freq: 868.3, chan: 22, lsnr: -3.0, rssi: -115.0, SF: SF7, BW: 125, codr: 

## Let's evaluate the results of the source code generated by Codestral.

In [ ]:
dataset_path = "prompt_Q1-2024-05-20/"
result_path = "codestral_source_code_results/"
evaluate_results(dataset_path,result_path)

Streaming output truncated to the last 5000 lines.

BLEU score: 0.5725114538460981
ROUGE-1: Score(precision=1.0, recall=1.0, fmeasure=1.0)
ROUGE-L: Score(precision=0.88, recall=0.88, fmeasure=0.88)



Sample:  prompt_n_hours=2_skip_hours=770.txt
For DEVICE dev_eui:120 all received frames are 2.
For DEVICE dev_eui:121 all received frames are 4.
For DEVICE dev_eui:122 all received frames are 2.
For DEVICE dev_eui:123 all received frames are 2.
For DEVICE dev_eui:124 all received frames are 2.
For DEVICE dev_eui:125 all received frames are 2.
For DEVICE dev_eui:126 all received frames are 2.
For DEVICE dev_eui:127 all received frames are 2.
For DEVICE dev_eui:128 all received frames are 6.
For DEVICE dev_eui:129 all received frames are 2.


For DEVICE dev_eui: 122 all received frames are 2.
For DEVICE dev_eui: 124 all received frames are 2.
For DEVICE dev_eui: 129 all received frames are 2.
For DEVICE dev_eui: 121 all received frames are 4.
For DEVICE dev_eui: 123 all received frames are 

#Let's evaluate the correctness of the responses in terms of Precision and Recall.

In [ ]:
def calculate_precision_recall (dataset_path,result_path):
  total_true_positive = 0
  total_false_positive = 0
  total_false_negative = 0
  # Iterate through all the test_files
  for filename in test_set:
      # Specify the paths to the files
      file1_path = result_path+filename
      file2_path = dataset_path+filename

      # Read the contents of the files
      try:
        with open(file1_path, 'r', encoding='utf-8') as file1:
          text1 = file1.read()
      except:
        continue
      try:
        with open(file2_path, 'r', encoding='utf-8') as file2:
          text2 = file2.read()
      except:
        continue

      # Find the index where "ANSWER:" starts
      answer_start_index = text2.find("ANSWER:")

      # Remove all content before and excluding "ANSWER:"
      if answer_start_index != -1:
          text2 = text2[answer_start_index + len("ANSWER:"):].strip()

      print("Sample: ", filename)

      #print(text2)
      #print("\n")
      #print(text1)

      # text1 contains results. text2 contains the correct values.
      # Create a dictionary for both text files. Key is the dev_eui and value is the number of frames.

      # For each line in text1 create a pair key value. key is the number of dev_eui, and value is the number of frames.
      results_dict = {}
      target_dict = {}

      #print(text1)

      # Split the data into lines
      lines = text1.split('\n')

      #print(lines)

      for line in lines:
        parts = line.split()
        try:
          # Usa regex per estrarre il dev_eui e il numero di frames
          match = re.search(r"dev_eui:\s*(\d+).*frames are (\d+)", line)

          if match:
              dev_eui = match.group(1)  # Il primo numero catturato (128)
              frames = match.group(2)    # Il secondo numero catturato (2)
        except:
          continue

        # Add to dictionary
        try:
          results_dict[dev_eui] = int(frames)
        except:
          results_dict[dev_eui] = 0

      # Split the data into lines
      lines = text2.split('\n')

      #print(lines)

      for line in lines:
        #print(line)
        # Split the line to extract dev_eui and frames
        parts = line.split()
        try:
          dev_eui = parts[2].split(':')[1]
          frames = parts[7].split('.')[0]
        except:
          continue

        # Add to dictionary
        try:
          target_dict[dev_eui] = int(frames)
        except:
          target_dict[dev_eui] = 0

      print(results_dict)
      print(target_dict)

      # Let's count the true positive.
      true_positive = 0
      for key in results_dict:
        if key in target_dict:
          if results_dict[key] == target_dict[key]:
            true_positive += 1
      print("True positive so far: ",true_positive)


      # Let's count the false positive.
      false_positive = 0
      for key in results_dict:
        if key not in target_dict:
          false_positive += 1
        else:
          if key in target_dict and results_dict[key] != target_dict[key]:
            false_positive += 1
      print("False positive so far: ",false_positive)

      # Let's count the false negative.
      false_negative = 0
      for key in target_dict:
        if key not in results_dict:
          false_negative += 1
      print("False negative so far: ",false_negative)

      total_true_positive += true_positive
      total_false_positive += false_positive
      total_false_negative += false_negative

  print("The precision is: ",total_true_positive/(total_true_positive+total_false_positive))
  print("The recall is: ",total_true_positive/(total_true_positive+total_false_negative))

##Let's evaluate Codestral

In [ ]:
dataset_path = "prompt_Q1-2024-05-20/"
result_path = "codestral_results/"
calculate_precision_recall(dataset_path,result_path)

Sample:  prompt_n_hours=2_skip_hours=248.txt
{'11': 0, '19': 0, '31': 0, '48': 0, '49': 0, '58': 0, '00': 0, '02': 0}
{'120': 1, '121': 2, '123': 3, '127': 1, '128': 2}
True positive so far:  0
False positive so far:  8
False negative so far:  5
Sample:  prompt_n_hours=2_skip_hours=786.txt
{'120': 2, '121': 2, '122': 3, '123': 2, '124': 3, '125': 2, '126': 2, '127': 2, '128': 6, '129': 4}
{'120': 2, '121': 2, '122': 2, '123': 2, '124': 4, '125': 2, '126': 2, '127': 2, '128': 5, '129': 4}
True positive so far:  7
False positive so far:  3
False negative so far:  0
Sample:  prompt_n_hours=2_skip_hours=1078.txt
{'120': 2, '121': 1, '122': 2, '123': 1, '124': 3, '125': 2, '126': 2, '127': 2, '128': 1, '129': 2}
{'120': 2, '121': 2, '122': 2, '123': 1, '124': 4, '125': 2, '126': 2, '127': 2, '128': 2, '129': 2}
True positive so far:  7
False positive so far:  3
False negative so far:  0
Sample:  prompt_n_hours=2_skip_hours=686.txt
{'120': 2, '121': 2, '122': 2, '123': 2, '124': 4, '125': 2,

## Let's evaluate Codestral with CoC (Chain of Code)

In [ ]:
dataset_path = "prompt_Q1-2024-05-20/"
result_path = "codestral_source_code_results/"
calculate_precision_recall(dataset_path,result_path)

Sample:  prompt_n_hours=2_skip_hours=324.txt
{'122': 2, '124': 4, '129': 2, '123': 2, '127': 3, '120': 2, '125': 3, '126': 2, '128': 9, '121': 2}
{'120': 2, '121': 2, '122': 1, '123': 1, '124': 5, '126': 5, '127': 2, '128': 5}
True positive so far:  2
False positive so far:  8
False negative so far:  0
Sample:  prompt_n_hours=2_skip_hours=274.txt
{'126': 2, '122': 1, '124': 6, '123': 2, '121': 2, '127': 2, '120': 3, '128': 3}
{'120': 3, '121': 2, '122': 1, '123': 2, '124': 6, '126': 2, '127': 2, '128': 3}
True positive so far:  8
False positive so far:  0
False negative so far:  0
Sample:  prompt_n_hours=2_skip_hours=986.txt
{'124': 3, '122': 3, '129': 2, '121': 2, '123': 2, '127': 2, '120': 2, '125': 2, '126': 2, '128': 2}
{'120': 2, '121': 2, '122': 3, '123': 2, '124': 3, '125': 2, '126': 2, '127': 2, '128': 2, '129': 2}
True positive so far:  10
False positive so far:  0
False negative so far:  0
Sample:  prompt_n_hours=2_skip_hours=686.txt
{'122': 2, '124': 4, '129': 4, '121': 2, '

# Zip and download the results using the two approaches.

In [ ]:
!zip -r codestral_results.zip codestral_results
!zip -r codestral_source_code_results.zip codestral_source_code_results

updating: codestral_results/ (stored 0%)
updating: codestral_results/prompt_n_hours=2_skip_hours=74.txt (deflated 79%)
updating: codestral_results/prompt_n_hours=2_skip_hours=100.txt (deflated 77%)
updating: codestral_results/prompt_n_hours=2_skip_hours=36.txt (deflated 78%)
updating: codestral_results/prompt_n_hours=2_skip_hours=760.txt (deflated 82%)
updating: codestral_results/prompt_n_hours=2_skip_hours=578.txt (deflated 79%)
updating: codestral_results/prompt_n_hours=2_skip_hours=412.txt (deflated 75%)
updating: codestral_results/prompt_n_hours=2_skip_hours=456.txt (deflated 79%)
updating: codestral_results/prompt_n_hours=2_skip_hours=972.txt (deflated 81%)
updating: codestral_results/prompt_n_hours=2_skip_hours=438.txt (deflated 81%)
updating: codestral_results/prompt_n_hours=2_skip_hours=586.txt (deflated 80%)
updating: codestral_results/prompt_n_hours=2_skip_hours=4.txt (deflated 79%)
updating: codestral_results/prompt_n_hours=2_skip_hours=294.txt (deflated 77%)
updating: codes